In [2]:
import datatoolbox as dt
import pyam as pyam
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

0 source reader found and added into "datatoolbox.sources".


<IPython.core.display.Javascript object>

## Analysing reduction levels in 1.5 pathways

In [190]:
iam_data_15_co2 = pyam.read_iiasa('iamc15', region = 'World',
                          variable = 'Emissions|CO2')
iam_data_15_ghg = pyam.read_iiasa('iamc15', region = 'World',
                          variable = 'Emissions|Kyoto Gases (AR4-GWP100)')

iam_data_15_lu = pyam.read_iiasa('iamc15', region = 'World',
                          variable = 'Emissions|CO2|AFOLU')


pyam.iiasa - INFO: You are connected to the IXSE_SR15 scenario explorer hosted by IIASA. If you use this data in any published format, please cite the data as provided in the explorer guidelines: https://data.ene.iiasa.ac.at/iamc-1.5c-explorer/#/about
pyam.iiasa - INFO: You are connected as an anonymous user
pyam.iiasa - INFO: You are connected to the IXSE_SR15 scenario explorer hosted by IIASA. If you use this data in any published format, please cite the data as provided in the explorer guidelines: https://data.ene.iiasa.ac.at/iamc-1.5c-explorer/#/about
pyam.iiasa - INFO: You are connected as an anonymous user
pyam.iiasa - INFO: You are connected to the IXSE_SR15 scenario explorer hosted by IIASA. If you use this data in any published format, please cite the data as provided in the explorer guidelines: https://data.ene.iiasa.ac.at/iamc-1.5c-explorer/#/about
pyam.iiasa - INFO: You are connected as an anonymous user


In [192]:
# Filtered pathway scenarios
filtered = pd.read_csv('ca_sustainable_scenarios.csv')

In [219]:
filtered

model                           scenario  exclude
0             AIM/CGE 2.0                            SSP2-19     True
1             AIM/CGE 2.1  TERL_15D_LowCarbonTransportPolicy     True
2           C-ROADS-5.005                  Ratchet-1.5-noCDR     True
3           C-ROADS-5.005             Ratchet-1.5-noCDR-noOS     True
4             IMAGE 3.0.1                       IMA15-LiStCh     True
5             IMAGE 3.0.1                            SSP1-19     True
6     MESSAGE-GLOBIOM 1.0                            SSP1-19     True
7     MESSAGE-GLOBIOM 1.0                            SSP2-19     True
8   MESSAGEix-GLOBIOM 1.0                    LowEnergyDemand     True
9             POLES EMF33                 EMF33_1.5C_cost100     True
10            POLES EMF33                    EMF33_1.5C_full     True
11            POLES EMF33                  EMF33_1.5C_limbio     True
12            POLES EMF33                  EMF33_1.5C_nofuel     True
13            POLES EMF33                 EMF33_WB2C_cost100     True
14            POLES EMF33                  EMF33_WB2C_limbio     True
15            POLES EMF33                 EMF33_WB2C_nobeccs     True
16            POLES EMF33                  EMF33_WB2C_nofuel     True
17            POLES EMF33                    EMF33_WB2C_none     True
18             REMIND 1.7                    CEMICS-1.5-CDR8     True
19      WITCH-GLOBIOM 4.4               CD-LINKS_NPi2020_400     True

In [193]:
pathways_ghg = iam_data_15_ghg.filter(category = ['Below 1.5C', '1.5C low overshoot'])
pathways_co2 = iam_data_15_co2.filter(category = ['Below 1.5C', '1.5C low overshoot'])
pathways_lu = iam_data_15_lu.filter(category = ['Below 1.5C', '1.5C low overshoot'])

In [181]:
# To filter:
pathways_co2.load_meta("ca_sustainable_scenarios.csv")
pathways_ghg.load_meta("ca_sustainable_scenarios.csv")
pathways_lu.load_meta("ca_sustainable_scenarios.csv")

pathways_co2_filt = pathways_co2.filter(exclude = True)
pathways_ghg_filt = pathways_ghg.filter(exclude = True)
pathways_lu_filt = pathways_lu.filter(exclude = True)

pyam.core - INFO: Importing meta indicators for 20 scenarios (for total of 53)
pyam.core - INFO: Importing meta indicators for 20 scenarios (for total of 47)
pyam.core - INFO: Importing meta indicators for 20 scenarios (for total of 53)


In [212]:
def find_stats(pathways_co2, pathways_ghg, pathways_lu):
    
    filt_ghg = pathways_ghg.timeseries()
    filt_co2= pathways_co2.timeseries()
    filt_lu = pathways_lu.timeseries()
    pathways_lu_eq = pathways_lu.convert_unit('Mt CO2/yr', to = 'Mt CO2-equiv/yr')
    
    a = pathways_co2.filter(variable="Emissions|CO2")._data.droplevel("variable")
    b = pathways_lu.filter(variable="Emissions|CO2|AFOLU")._data.droplevel("variable")
    result = pyam.IamDataFrame(a - b, variable="CO2_noAFOLU")
    co2_nolu_series = result.timeseries()
    compare_co2_nolu = co2_nolu_series[2030] / co2_nolu_series[2010] * 100

    a = pathways_ghg.filter(variable="Emissions|Kyoto Gases (AR4-GWP100)")._data.droplevel("variable")
    b = pathways_lu_eq.filter(variable="Emissions|CO2|AFOLU")._data.droplevel("variable")
    result = pyam.IamDataFrame(a - b, variable="GHG_noAFOLU")
    ghg_nolu_series = result.timeseries()
    compare_ghg_nolu = ghg_nolu_series[2030] / ghg_nolu_series[2010] * 100
    
    compare_co2 = filt_co2[2030] / filt_co2[2010]*100
    compare_ghg = filt_ghg[2030] / filt_ghg[2010]*100
    
    co2 = 100 - np.percentile(compare_co2,[50, 25, 75])
    ghg = 100 - np.percentile(compare_ghg,[50, 25, 75])
    co2_nolu = 100 - np.percentile(compare_co2_nolu,[50, 25, 75])
    ghg_nolu = 100 - np.percentile(compare_ghg_nolu,[50, 25, 75])
    
    ghg_2030 = np.percentile(ghg_nolu_series[2030],[50, 25, 75])
    pd.Data
    return(co2, ghg, co2_nolu, ghg_nolu, ghg_2030)
    

In [213]:
with_filters = find_stats(pathways_co2_filt, pathways_ghg_filt, pathways_lu_filt)
print(with_filters[0:5])

no_filters = find_stats(pathways_co2, pathways_ghg, pathways_lu)
print(no_filters[0:5])

(array([51.87086399, 60.70108796, 41.52112777]), array([49.43110323, 56.38805332, 39.2470201 ]), array([42.67461495, 52.28010326, 30.81882904]), array([43.41705238, 49.25178407, 32.36960276]), array([25335.71448315, 22812.86260975, 30130.0615842 ]))
(array([45.58881003, 58.90345434, 40.25862868]), array([45.79594533, 54.58340818, 37.75399871]), array([38.28646879, 50.15621219, 30.88933733]), array([38.62325866, 45.97057305, 30.84050826]), array([27476.48719  , 24132.0585445, 31860.1597895]))


In [233]:
pd.DataFrame(no_filters, index = ['co2','ghg','co2_nolu','ghg_nolu','ghg_2030'], columns = ['50%', '25%', '75%'])

50%           25%           75%
co2          45.588810     58.903454     40.258629
ghg          45.795945     54.583408     37.753999
co2_nolu     38.286469     50.156212     30.889337
ghg_nolu     38.623259     45.970573     30.840508
ghg_2030  27476.487190  24132.058544  31860.159790

In [234]:
pd.DataFrame(with_filters, index = ['co2','ghg','co2_nolu','ghg_nolu','ghg_2030'], columns = ['50%', '25%', '75%'])

50%           25%           75%
co2          51.870864     60.701088     41.521128
ghg          49.431103     56.388053     39.247020
co2_nolu     42.674615     52.280103     30.818829
ghg_nolu     43.417052     49.251784     32.369603
ghg_2030  25335.714483  22812.862610  30130.061584

In [228]:
# Find emissions in 2030 in pathways (median, 25th and 75th percentiles)
with_filters[4]  

array([25335.71448315, 22812.86260975, 30130.0615842 ])

In [226]:
# Calculate change from original NDC level
#(Is this a good source?)
catfinal_old = pd.read_excel('../tool/Data prep/Data/CATFINAL_190823_data.xlsx', header = 28, sheet_name= 'CATFINAL_NDCA0_CATM0EL').set_index('Countries\Years')

In [157]:
catold_ndc_2030 = catfinal_old.loc['EARTH', 2030]
print(catold_ndc_2030)

51619.91


In [217]:
print(1 - with_filters[4]/catold_ndc_2030)
print(1 - no_filters[4]/catold_ndc_2030)

[0.50918716 0.55806078 0.4163093 ]
[0.46771532 0.53250483 0.38279319]


In [ ]:
#OLD - ignore

In [199]:
pathways_lu_eq = pathways_lu.convert_unit('Mt CO2/yr', to = 'Mt CO2-equiv/yr')

In [200]:
a = pathways_co2.filter(variable="Emissions|CO2")._data.droplevel("variable")
b = pathways_lu.filter(variable="Emissions|CO2|AFOLU")._data.droplevel("variable")
result = pyam.IamDataFrame(a - b, variable="CO2_noAFOLU")
co2_nolu_series = result.timeseries()
compare_co2_nolu = co2_nolu_series[2030] / co2_nolu_series[2010] * 100

a = pathways_ghg.filter(variable="Emissions|Kyoto Gases (AR4-GWP100)")._data.droplevel("variable")
b = pathways_lu_eq.filter(variable="Emissions|CO2|AFOLU")._data.droplevel("variable")
result = pyam.IamDataFrame(a - b, variable="GHG_noAFOLU")
ghg_nolu_series = result.timeseries()
compare_ghg_nolu = ghg_nolu_series[2030] / ghg_nolu_series[2010] * 100

In [201]:
compare_co2 = filt_co2[2030] / filt_co2[2010]*100
compare_ghg = filt_ghg[2030] / filt_ghg[2010]*100

In [202]:
co2 = 100 - np.percentile(compare_co2,[50, 25, 75])
ghg = 100 - np.percentile(compare_ghg,[50, 25, 75])
co2_nolu = 100 - np.percentile(compare_co2_nolu,[50, 25, 75])
ghg_nolu = 100 - np.percentile(compare_ghg_nolu,[50, 25, 75])

Kyoto gases (SAR) for all no / low overshoot pathways: 46% below 2010
Kyoto gases (AR4) for all no / low overshoot pathways: 46% below 2010
CO2: 46% (45.59%) below 2010

In [203]:
print(ghg_nolu)
print(ghg)


[38.62325866 45.97057305 30.84050826]
[49.43110323 56.38805332 39.2470201 ]


In [167]:
stats_2030_15 = np.percentile(ghg_nolu_series[2030],[50, 25, 75])

In [171]:
1 - stats_2030_15 / catold_ndc_2030

array([0.50918716, 0.55806078, 0.4163093 ])